# A Guide to TF Layers: Building a Convolutional Neural Network
https://www.tensorflow.org/tutorials/layers

The TensorFlow layers module provides a high-level API that makes it easy to construct a neural network.
It provides methods that facilitate the creation of dense (fully connected) layers and convolutional layers, adding activation functions, and applying dropout regularization.
In this tutorial, you'll learn how to use layers to build a convolutional neural network model to recognize the handwritten digits in the MNIST data set.


![handwritten digits 0–9 from the MNIST data set](mnist_0-9.png)


The MNIST dataset comprises 60,000 training examples and 10,000 test examples of the handwritten digits 0–9, formatted as 28x28-pixel monochrome images.

## Getting Started
Let's set up the skeleton for our TensorFlow program.
Create a file called cnn_mnist.py, and add the following code:
https://github.com/tensorflow/tensorflow/blob/r1.4/tensorflow/examples/tutorials/layers/cnn_mnist.py

In [1]:
# Imports
import numpy as np
import tensorflow as tf
from tensorflow.examples.tutorials.mnist import input_data

tf.logging.set_verbosity(tf.logging.INFO)

## Intro to Convolutional Neural Networks
Convolutional neural networks (CNNs) are the current state-of-the-art model architecture for image classification tasks.
CNNs apply a series of filters to the raw pixel data of an image to extract and learn higher-level features, which the model can then use for classification.
CNNs contains three components:

- Convolutional layers, which apply a specified number of convolution filters to the image. For each subregion, the layer performs a set of mathematical operations to produce a single value in the output feature map. Convolutional layers then typically apply a ReLU activation function to the output to introduce nonlinearities into the model.

- Pooling layers, which downsample the image data extracted by the convolutional layers to reduce the dimensionality of the feature map in order to decrease processing time. A commonly used pooling algorithm is max pooling, which extracts subregions of the feature map (e.g., 2x2-pixel tiles), keeps their maximum value, and discards all other values.

- Dense (fully connected) layers, which perform classification on the features extracted by the convolutional layers and downsampled by the pooling layers. In a dense layer, every node in the layer is connected to every node in the preceding layer.

Typically, a CNN is composed of a stack of convolutional modules that perform feature extraction.
Each module consists of a convolutional layer followed by a pooling layer.
The last convolutional module is followed by one or more dense layers that perform classification.
The final dense layer in a CNN contains a single node for each target class in the model (all the possible classes the model may predict), with a softmax activation function to generate a value between 0–1 for each node (the sum of all these softmax values is equal to 1).
We can interpret the softmax values for a given image as relative measurements of how likely it is that the image falls into each target class.

More info: https://cs231n.github.io/convolutional-networks/

## Building the CNN MNIST Classifier
Let's build a model to classify the images in the MNIST dataset using the following CNN architecture:

1. Convolutional Layer #1: Applies 32 5x5 filters (extracting 5x5-pixel subregions), with ReLU activation function
2. Pooling Layer #1: Performs max pooling with a 2x2 filter and stride of 2 (which specifies that pooled regions do not overlap)
3. Convolutional Layer #2: Applies 64 5x5 filters, with ReLU activation function
4. Pooling Layer #2: Again, performs max pooling with a 2x2 filter and stride of 2
5. Dense Layer #1: 1,024 neurons, with dropout regularization rate of 0.4 (probability of 0.4 that any given element will be dropped during training)
6. Dense Layer #2 (Logits Layer): 10 neurons, one for each digit target class (0–9).

The tf.layers module contains methods to create each of the three layer types above:

- conv2d(). Constructs a two-dimensional convolutional layer. Takes number of filters, filter kernel size, padding, and activation function as arguments.
- max_pooling2d(). Constructs a two-dimensional pooling layer using the max-pooling algorithm. Takes pooling filter size and stride as arguments.
- dense(). Constructs a dense layer. Takes number of neurons and activation function as arguments.

Each of these methods accepts a tensor as input and returns a transformed tensor as output.
This makes it easy to connect one layer to another: just take the output from one layer-creation method and supply it as input to another.

Open cnn_mnist.py and add the following cnn_model_fn function, which conforms to the interface expected by TensorFlow's Estimator API (more on this later in Create the Estimator).
cnn_mnist.py takes MNIST feature data, labels, and model mode (TRAIN, EVAL, PREDICT) as arguments; configures the CNN; and returns predictions, loss, and a training operation:

In [2]:
def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    # Reshape X to 4-D tensor: [batch_size, width, height, channels] == [NHWC]
    # MNIST images are 28x28 pixels, and have one color channel
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional Layer #1
    # Computes 32 features using a 5x5 filter with ReLU activation.
    # Padding is added to preserve width and height.
    # Input Tensor Shape: [batch_size, 28, 28, 1]
    # Output Tensor Shape: [batch_size, 28, 28, 32]
    conv1 = tf.layers.conv2d(inputs=input_layer, filters=32, kernel_size=[5, 5], padding="same", activation=tf.nn.relu)
    # tf.nn.conv2d(x, W, strides=[1, 1, 1, 1], padding='SAME') # same as above, here W: [filter_height, filter_width, in_channels, out_channels]
    
    """
    https://www.tensorflow.org/api_docs/python/tf/layers/conv2d
    tf.layers.conv2d
    conv2d(inputs, filters, kernel_size, strides=(1, 1), padding='valid', data_format='channels_last', dilation_rate=(1, 1),
    activation=None, use_bias=True, kernel_initializer=None, bias_initializer=tf.zeros_initializer(), kernel_regularizer=None,
    bias_regularizer=None, activity_regularizer=None, kernel_constraint=None, bias_constraint=None, trainable=True, name=None, reuse=None)
    
    Functional interface for the 2D convolution layer.
    This layer creates a convolution kernel that is convolved (actually cross-correlated) with the layer input
    to produce a tensor of outputs. If use_bias is True (and a bias_initializer is provided),
    a bias vector is created and added to the outputs. Finally, if activation is not None, it is applied to the outputs as well.
    """
    # Pooling Layer #1
    # First max pooling layer with a 2x2 filter and stride of 2
    # Input Tensor Shape: [batch_size, 28, 28, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 32]
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)
    # tf.nn.max_pool(x, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME') # same as above

    # Convolutional Layer #2
    # Computes 64 features using a 5x5 filter.
    # Padding is added to preserve width and height.
    # Input Tensor Shape: [batch_size, 14, 14, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 64]
    conv2 = tf.layers.conv2d(inputs=pool1, filters=64, kernel_size=[5, 5], padding="same", activation=tf.nn.relu)

    # Pooling Layer #2
    # Second max pooling layer with a 2x2 filter and stride of 2
    # Input Tensor Shape: [batch_size, 14, 14, 64]
    # Output Tensor Shape: [batch_size, 7, 7, 64]
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Flatten tensor into a batch of vectors
    # Input Tensor Shape: [batch_size, 7, 7, 64]
    # Output Tensor Shape: [batch_size, 7 * 7 * 64]
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

    # Dense Layer
    # Densely connected layer with 1024 neurons
    # Input Tensor Shape: [batch_size, 7 * 7 * 64]
    # Output Tensor Shape: [batch_size, 1024]
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

    # Add dropout operation; 0.6 probability that element will be kept
    dropout = tf.layers.dropout(inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits layer
    # Input Tensor Shape: [batch_size, 1024]
    # Output Tensor Shape: [batch_size, 10]
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    onehot_labels = tf.one_hot(indices=tf.cast(labels, tf.int32), depth=10)
    loss = tf.losses.softmax_cross_entropy(onehot_labels=onehot_labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(loss=loss, global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(labels=labels, predictions=predictions["classes"])
    }
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

The following sections (with headings corresponding to each code block above) dive deeper into the tf.layers code used to create each layer, as well as how to calculate loss, configure the training op, and generate predictions.
If you're already experienced with CNNs and TensorFlow Estimators, and find the above code intuitive, you may want to skim these sections or just skip ahead to "Training and Evaluating the CNN MNIST Classifier".

## Input Layer
The methods in the layers module for creating convolutional and pooling layers for two-dimensional image data expect input tensors to have a shape of [batch_size, image_width, image_height, channels], defined as follows:

batch_size. Size of the subset of examples to use when performing gradient descent during training.
image_width. Width of the example images.
image_height. Height of the example images.
channels. Number of color channels in the example images.
For color images, the number of channels is 3 (red, green, blue).
For monochrome images, there is just 1 channel (black).
Here, our MNIST dataset is composed of monochrome 28x28 pixel images, so the desired shape for our input layer is [batch_size, 28, 28, 1].

To convert our input feature map (features) to this shape, we can perform the following reshape operation:

input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])
Note that we've indicated -1 for batch size, which specifies that this dimension should be dynamically computed based on the number of input values in features["x"], holding the size of all other dimensions constant.
This allows us to treat batch_size as a hyperparameter that we can tune.
For example, if we feed examples into our model in batches of 5, features["x"] will contain 3,920 (28*28*5=3,920) values (one value for each pixel in each image), and input_layer will have a shape of [5, 28, 28, 1].
Similarly, if we feed examples in batches of 100, features["x"] will contain 78,400 values, and input_layer will have a shape of [100, 28, 28, 1].

## Convolutional Layer #1

In our first convolutional layer, we want to apply 32 5x5 filters to the input layer, with a ReLU activation function.
We can use the conv2d() method in the layers module to create this layer as follows:

conv1 = tf.layers.conv2d(inputs=input_layer, filters=32, kernel_size=[5, 5], padding="same", activation=tf.nn.relu)

The inputs argument specifies our input tensor, which must have the shape [batch_size, image_width, image_height, channels]. Here, we're connecting our first convolutional layer to input_layer, which has the shape [batch_size, 28, 28, 1].

Note: conv2d() will instead accept a shape of [channels, batch_size, image_width, image_height] when passed the argument data_format=channels_first.
The filters argument specifies the number of filters to apply (here, 32), and kernel_size specifies the dimensions of the filters as [width, height] (here, [5, 5]).

TIP: If filter width and height have the same value, you can instead specify a single integer for kernel_size—e.g., kernel_size=5.

The padding argument specifies one of two enumerated values (case-insensitive): valid (default value) or same.
To specify that the output tensor should have the same width and height values as the input tensor, we set padding=same here, which instructs TensorFlow to add 0 values to the edges of the input tensor to preserve width and height of 28. <u>(Without padding, a 5x5 convolution over a 28x28 tensor will produce a 24x24 tensor, as there are 24x24 locations to extract a 5x5 tile from a 28x28 grid.)</u>

The activation argument specifies the activation function to apply to the output of the convolution.
Here, we specify ReLU activation with tf.nn.relu.

<u>Our output tensor produced by conv2d() has a shape of [batch_size, 28, 28, 32]: the same width and height dimensions as the input, but now with 32 channels holding the output from each of the filters.</u>

## Pooling Layer #1
Next, we connect our first pooling layer to the convolutional layer we just created.
We can use the max_pooling2d() method in layers to construct a layer that performs max pooling with a 2x2 filter and stride of 2:

pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)
Again, inputs specifies the input tensor, with a shape of [batch_size, image_width, image_height, channels].
Here, our input tensor is conv1, the output from the first convolutional layer, which has a shape of [batch_size, 28, 28, 32].

Note: As with conv2d(), max_pooling2d() will instead accept a shape of [channels, batch_size, image_width, image_height] when passed the argument data_format=channels_first.

The pool_size argument specifies the size of the max pooling filter as [width, height] (here, [2, 2]).
If both dimensions have the same value, you can instead specify a single integer (e.g., pool_size=2).

The strides argument specifies the size of the stride.
Here, we set a stride of 2, which indicates that the subregions extracted by the filter should be separated by 2 pixels in both the width and height dimensions (for a 2x2 filter, this means that none of the regions extracted will overlap).
If you want to set different stride values for width and height, you can instead specify a tuple or list (e.g., stride=[3, 6]).

<u>Our output tensor produced by max_pooling2d() (pool1) has a shape of [batch_size, 14, 14, 32]: the 2x2 filter reduces width and height by 50% each.</u>

## Convolutional Layer #2 and Pooling Layer #2

We can connect a second convolutional and pooling layer to our CNN using conv2d() and max_pooling2d() as before.
For convolutional layer #2, we configure 64 5x5 filters with ReLU activation, and for pooling layer #2, we use the same specs as pooling layer #1 (a 2x2 max pooling filter with stride of 2):

conv2 = tf.layers.conv2d(inputs=pool1, filters=64, kernel_size=[5, 5], padding="same", activation=tf.nn.relu)

pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

Note that convolutional layer #2 takes the output tensor of our first pooling layer (pool1) as input, and produces the tensor conv2 as output.
conv2 has a shape of [batch_size, 14, 14, 64], the same width and height as pool1 (due to padding="same"), and 64 channels for the 64 filters applied.

Pooling layer #2 takes conv2 as input, producing pool2 as output. pool2 has shape [batch_size, 7, 7, 64] (50% reduction of width and height from conv2).

## Dense Layer

Next, we want to add a dense layer (with 1,024 neurons and ReLU activation) to our CNN to perform classification on the features extracted by the convolution/pooling layers.
Before we connect the layer, however, we'll flatten our feature map (pool2) to shape [batch_size, features], so that our tensor has only two dimensions:

pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

In the reshape() operation above, the -1 signifies that the batch_size dimension will be dynamically calculated based on the number of examples in our input data.
Each example has 7 (pool2 width) * 7 (pool2 height) * 64 (pool2 channels) features, so we want the features dimension to have a value of 7 * 7 * 64 (3136 in total).
The output tensor, pool2_flat, has shape [batch_size, 3136].

Now, we can use the dense() method in layers to connect our dense layer as follows:

dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

The inputs argument specifies the input tensor: our flattened feature map, pool2_flat.
<u>The units argument specifies the number of neurons in the dense layer (1,024).</u>
The activation argument takes the activation function; again, we'll use tf.nn.relu to add ReLU activation.

To help improve the results of our model, we also apply dropout regularization to our dense layer, using the dropout method in layers:

dropout = tf.layers.dropout(inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

Again, inputs specifies the input tensor, which is the output tensor from our dense layer (dense).

The rate argument specifies the dropout rate; here, we use 0.4, which means <u>40% of the elements will be randomly dropped out during training.</u>

<u>The training argument takes a boolean specifying whether or not the model is currently being run in training mode; dropout will only be performed if training is True.
Here, we check if the mode passed to our model function cnn_model_fn is TRAIN mode.</u>

Our output tensor dropout has shape [batch_size, 1024].

## Logits Layer
The final layer in our neural network is the logits layer, which will return the raw values for our predictions.
We create a dense layer with 10 neurons (one for each target class 0–9), with linear activation (the default):

logits = tf.layers.dense(inputs=dropout, units=10)

Our final output tensor of the CNN, logits, has shape [batch_size, 10].

## Generate Predictions

The logits layer of our model returns our predictions as raw values in a [batch_size, 10]-dimensional tensor.
Let's convert these raw values into two different formats that our model function can return:

The predicted class for each example: a digit from 0–9.
The probabilities for each possible target class for each example: the probability that the example is a 0, is a 1, is a 2, etc.
For a given example, our predicted class is the element in the corresponding row of the logits tensor with the highest raw value.
We can find the index of this element using the tf.argmax function:

tf.argmax(input=logits, axis=1)

The input argument specifies the tensor from which to extract maximum values—here logits.
The axis argument specifies the axis of the input tensor along which to find the greatest value.
Here, we want to find the largest value along the dimension with index of 1, which corresponds to our predictions (recall that our logits tensor has shape [batch_size, 10]).

We can derive probabilities from our logits layer by applying softmax activation using tf.nn.softmax:

tf.nn.softmax(logits, name="softmax_tensor")

Note: We use the name argument to explicitly name this operation softmax_tensor, so we can reference it later.
(We'll set up logging for the softmax values in "Set Up a Logging Hook".
We compile our predictions in a dict, and return an EstimatorSpec object:

    predictions = {
        "classes": tf.argmax(input=logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    if mode == tf.estimator.ModeKeys.PREDICT:
      return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)


## Calculate Loss

For both training and evaluation, we need to define a loss function that measures how closely the model's predictions match the target classes.
For multiclass classification problems like MNIST, cross entropy is typically used as the loss metric.
The following code calculates cross entropy when the model runs in either TRAIN or EVAL mode:

    onehot_labels = tf.one_hot(indices=tf.cast(labels, tf.int32), depth=10)
    loss = tf.losses.softmax_cross_entropy(onehot_labels=onehot_labels, logits=logits)

Let's take a closer look at what's happening above.

Our labels tensor contains a list of predictions for our examples, e.g. [1, 9, ...].
In order to calculate cross-entropy, first we need to convert labels to the corresponding one-hot encoding:

[[0, 1, 0, 0, 0, 0, 0, 0, 0, 0],
 [0, 0, 0, 0, 0, 0, 0, 0, 0, 1],
 ...]

We use the tf.one_hot function to perform this conversion. tf.one_hot() has two required arguments:

indices. The locations in the one-hot tensor that will have "on values"—i.e., the locations of 1 values in the tensor shown above.
depth. The depth of the one-hot tensor—i.e., the number of target classes. Here, the depth is 10.
The following code creates the one-hot tensor for our labels, onehot_labels:

onehot_labels = tf.one_hot(indices=tf.cast(labels, tf.int32), depth=10)

Because labels contains a series of values from 0–9, indices is just our labels tensor, with values cast to integers.
The depth is 10 because we have 10 possible target classes, one for each digit.

Next, we compute cross-entropy of onehot_labels and the softmax of the predictions from our logits layer. tf.losses.softmax_cross_entropy() takes onehot_labels and logits as arguments, performs softmax activation on logits, calculates cross-entropy, and returns our loss as a scalar Tensor:

loss = tf.losses.softmax_cross_entropy(onehot_labels=onehot_labels, logits=logits)

## Configure the Training Op

In the previous section, we defined loss for our CNN as the softmax cross-entropy of the logits layer and our labels.
Let's configure our model to optimize this loss value during training.
We'll use a learning rate of 0.001 and stochastic gradient descent as the optimization algorithm:

    if mode == tf.estimator.ModeKeys.TRAIN:
      optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
      train_op = optimizer.minimize(
          loss=loss,
          global_step=tf.train.get_global_step())
      return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

Note: For a more in-depth look at configuring training ops for Estimator model functions, see "Defining the training op for the model" in the "Creating Estimations in tf.estimator" tutorial.

## Add evaluation metrics

To add accuracy metric in our model, we define eval_metric_ops dict in EVAL mode as follows:

    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
            labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [3]:
def main(unused_argv):
    # Load training and eval data
    #mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    mnist = input_data.read_data_sets('../../../Datasets/MNIST_data/')
    train_data = mnist.train.images  # Returns np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images  # Returns np.array
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

    # Create the Estimator
    mnist_classifier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="mnist_convnet_model_logs")

    # Set up logging for predictions
    # Log the values in the "Softmax" tensor with label "probabilities"
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)

    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(x={"x": train_data}, y=train_labels, batch_size=100, num_epochs=None, shuffle=True)
    mnist_classifier.train(input_fn=train_input_fn, steps=20000, hooks=[logging_hook])

    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(x={"x": eval_data}, y=eval_labels, num_epochs=1, shuffle=False)
    
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print("eval_results: ", eval_results)

if __name__ == "__main__":
    tf.app.run()

Extracting ../../../Datasets/MNIST_data/train-images-idx3-ubyte.gz
Extracting ../../../Datasets/MNIST_data/train-labels-idx1-ubyte.gz
Extracting ../../../Datasets/MNIST_data/t10k-images-idx3-ubyte.gz
Extracting ../../../Datasets/MNIST_data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_num_ps_replicas': 0, '_num_worker_replicas': 1, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x000001A6CAFE7710>, '_tf_random_seed': None, '_save_summary_steps': 100, '_service': None, '_task_id': 0, '_session_config': None, '_keep_checkpoint_max': 5, '_log_step_count_steps': 100, '_keep_checkpoint_every_n_hours': 10000, '_save_checkpoints_secs': 600, '_master': '', '_save_checkpoints_steps': None, '_task_type': 'worker', '_model_dir': 'mnist_convnet_model_logs', '_is_chief': True}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into mnist_convnet_model_logs\model.ckpt.
INFO:tensorflow:

INFO:tensorflow:loss = 2.2994387, step = 1
INFO:tensorflow:probabilities = [[0.10620335 0.10933745 0.10504483 0.09867851 0.08813702 0.08513207
  0.11430068 0.09755402 0.10380303 0.091809  ]
 [0.09813183 0.09908269 0.1048973  0.09928112 0.09419441 0.08435696
  0.09391975 0.09802638 0.125933   0.10217645]
 [0.10261299 0.10268585 0.097438   0.09050378 0.09517647 0.08288782
  0.11466557 0.09687521 0.12488455 0.09226976]
 [0.1073551  0.09411304 0.11474655 0.09347992 0.07736102 0.10125052
  0.10376278 0.10252885 0.10764374 0.09775849]
 [0.10325622 0.10417414 0.10941098 0.09639301 0.09204265 0.08067553
  0.10839963 0.10179886 0.107113   0.09673585]
 [0.10983771 0.10218996 0.10111995 0.08817845 0.09478262 0.08597581
  0.11088121 0.09373591 0.11538257 0.09791582]
 [0.1257748  0.08666723 0.09031307 0.08161307 0.09798908 0.08318584
  0.1365742  0.09502189 0.10324524 0.09961563]
 [0.11200833 0.1107434  0.09846959 0.07892002 0.08216368 0.0957092
  0.09531785 0.11052179 0.1195339  0.09661219]
 [0.11

INFO:tensorflow:global_step/sec: 42.8848
INFO:tensorflow:probabilities = [[0.1046591  0.11287382 0.09161575 0.08749819 0.10905264 0.09321136
  0.09649033 0.11005575 0.10237699 0.09216605]
 [0.11522907 0.09579644 0.09591231 0.07974902 0.09399604 0.09174014
  0.11421811 0.09687726 0.10927467 0.10720688]
 [0.09448469 0.10483287 0.09620551 0.08939143 0.09471017 0.09086895
  0.11247716 0.09600767 0.12234174 0.09867971]
 [0.09589317 0.088794   0.10428168 0.11205368 0.08941714 0.09484543
  0.10996822 0.0972804  0.10440308 0.1030632 ]
 [0.11836925 0.08638094 0.09899136 0.09929793 0.08758282 0.08945449
  0.11450361 0.09973713 0.11623222 0.08945028]
 [0.124347   0.09392727 0.11197102 0.08845982 0.08712318 0.08332689
  0.10591289 0.09431299 0.11099936 0.09961952]
 [0.10354592 0.11306874 0.11024399 0.09510092 0.07526174 0.09983104
  0.11316255 0.08863597 0.10682582 0.09432331]
 [0.10877485 0.07994735 0.09586128 0.1054464  0.09380428 0.08866689
  0.12853906 0.09789046 0.1057325  0.09533709]
 [0.114

INFO:tensorflow:loss = 2.2765064, step = 101 (2.345 sec)
INFO:tensorflow:probabilities = [[0.11094321 0.08988577 0.09845264 0.10006025 0.08694991 0.08989708
  0.12214019 0.09964929 0.10559822 0.09642347]
 [0.12155985 0.10109157 0.10093921 0.07842629 0.0931074  0.09383162
  0.11083163 0.09584339 0.10085787 0.10351118]
 [0.10848035 0.09993435 0.11330871 0.10699353 0.08583453 0.07760265
  0.1097826  0.1067941  0.09681428 0.09445494]
 [0.11110497 0.08716465 0.11086344 0.09817386 0.10584023 0.08135781
  0.10243783 0.09629451 0.11289982 0.09386283]
 [0.09985714 0.10335645 0.09275435 0.09120325 0.09427767 0.08697
  0.10309675 0.09739256 0.11736185 0.11373001]
 [0.12952283 0.10110927 0.10505444 0.10290626 0.09568384 0.08176642
  0.1117276  0.08602586 0.10332139 0.08288206]
 [0.10819269 0.10430082 0.09871755 0.09098107 0.09162019 0.08005103
  0.10986683 0.10525597 0.11289714 0.09811672]
 [0.10782102 0.10454631 0.09886405 0.10668458 0.08789905 0.09139082
  0.10168879 0.0998582  0.10260142 0.0986

INFO:tensorflow:global_step/sec: 45.9081
INFO:tensorflow:probabilities = [[0.11253314 0.09833337 0.09611053 0.08571827 0.09653996 0.08823084
  0.09782344 0.10587636 0.09811282 0.12072115]
 [0.11109839 0.08924794 0.10393775 0.09516334 0.09180623 0.08719251
  0.10725808 0.10655355 0.10168992 0.1060523 ]
 [0.11066085 0.10499281 0.09379999 0.09287955 0.08937915 0.09046461
  0.11616758 0.1042327  0.11168642 0.08573636]
 [0.10036582 0.08548535 0.10792162 0.10251958 0.09136563 0.09383719
  0.09868957 0.11625405 0.11453865 0.08902251]
 [0.1126433  0.09292473 0.09726325 0.09457189 0.0829781  0.10196682
  0.09722845 0.11951796 0.10822051 0.09268493]
 [0.10412588 0.09263304 0.10651445 0.09198015 0.10498485 0.08703001
  0.11380041 0.08668946 0.10900884 0.10323296]
 [0.11752556 0.10031635 0.09470435 0.08783864 0.09266937 0.08678853
  0.09634257 0.11429489 0.10641555 0.10310423]
 [0.11660014 0.08589932 0.10606541 0.10371488 0.07546131 0.09662502
  0.11814804 0.10500123 0.09956606 0.09291863]
 [0.104

...

INFO:tensorflow:global_step/sec: 47.7327
INFO:tensorflow:probabilities = [[0.0001302  0.05312916 0.00447886 0.00128568 0.00725314 0.05635062
  0.08392234 0.00000041 0.7925305  0.00091919]
 [0.99965215 0.00000008 0.00007583 0.00002023 0.00000004 0.00017096
  0.00007313 0.0000007  0.00000648 0.00000032]
 [0.0000011  0.00000216 0.00002041 0.00059227 0.00002984 0.0003033
  0.00005051 0.00000008 0.99420565 0.00479472]
 [0.85916424 0.00000886 0.00679645 0.04486526 0.00025737 0.03061329
  0.00063429 0.00006218 0.05715309 0.000445  ]
 [0.00000048 0.00000019 0.00001164 0.00000009 0.9998591  0.00000135
  0.00004504 0.00000362 0.00001657 0.00006198]
 [0.00000007 0.00000001 0.00000017 0.00000053 0.00000002 0.00000003
  0.         0.9994056  0.0003207  0.00027279]
 [0.00009998 0.00231631 0.00138156 0.01277858 0.15387554 0.00247502
  0.00037516 0.00140369 0.454633   0.37066114]
 [0.0000643  0.0002262  0.00011082 0.00040374 0.1337893  0.0001947
  0.00004839 0.00507603 0.00103358 0.8590529 ]
 [0.00000

INFO:tensorflow:loss = 0.09197425, step = 19901 (2.089 sec)
INFO:tensorflow:probabilities = [[0.00061046 0.04308335 0.00212248 0.01341709 0.00003817 0.00459239
  0.00139561 0.00000815 0.93433017 0.00040211]
 [0.00000004 0.00000006 0.0000083  0.00003495 0.00000001 0.00000011
  0.         0.9998858  0.0000024  0.00006828]
 [0.00000117 0.00000002 0.00000002 0.00000419 0.00000036 0.99997544
  0.00000013 0.00000001 0.00001865 0.00000007]
 [0.00028369 0.00000018 0.00006569 0.00083297 0.00110085 0.00000844
  0.00000041 0.00330335 0.00034288 0.9940615 ]
 [0.0004726  0.02586669 0.00042001 0.00049823 0.00003371 0.0006655
  0.00006232 0.00005623 0.97164017 0.00028447]
 [0.00000006 0.0000233  0.9997024  0.00023648 0.         0.00000022
  0.00000004 0.0000082  0.00002937 0.        ]
 [0.00000007 0.0000154  0.00000197 0.00000473 0.9995685  0.00006892
  0.00000268 0.00015928 0.00004799 0.00013049]
 [0.00005605 0.00008274 0.00004755 0.00190267 0.00055549 0.66357356
  0.00000364 0.04161341 0.00410356 0

INFO:tensorflow:Saving checkpoints for 20000 into mnist_convnet_model_logs\model.ckpt.
INFO:tensorflow:Loss for final step: 0.17831671.
INFO:tensorflow:Starting evaluation at 2018-03-17-17:24:06
INFO:tensorflow:Restoring parameters from mnist_convnet_model_logs\model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-03-17-17:24:08
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9683, global_step = 20000, loss = 0.10339005
eval_results:  {'loss': 0.10339005, 'accuracy': 0.9683, 'global_step': 20000}


SystemExit: 

c:\anaconda2\envs\py3\lib\site-packages\IPython\core\interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


## Training and Evaluating the CNN MNIST Classifier

We've coded our MNIST CNN model function; now we're ready to train and evaluate it.

### Load Training and Test Data
First, let's load our training and test data.
Add a main() function to cnn_mnist.py with the following code:

    def main(unused_argv):
      mnist = tf.contrib.learn.datasets.load_dataset("mnist")
      train_data = mnist.train.images # Returns np.array
      train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
      eval_data = mnist.test.images # Returns np.array
      eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
  
We store the training feature data (the raw pixel values for 55,000 images of hand-drawn digits) and training labels (the corresponding value from 0–9 for each image) as numpy arrays in train_data and train_labels, respectively.
Similarly, we store the evaluation feature data (10,000 images) and evaluation labels in eval_data and eval_labels, respectively.

## Create the Estimator

Next, let's create an <u>Estimator (a TensorFlow class for performing high-level model training, evaluation, and inference)</u> for our model.
Add the following code to main():

# Create the Estimator

mnist_classifier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

The model_fn argument specifies the model function to use for training, evaluation, and prediction; we pass it the cnn_model_fn we created in "Building the CNN MNIST Classifier."
The model_dir argument specifies the directory where model data (checkpoints) will be saved (here, we specify the temp directory /tmp/mnist_convnet_model, but feel free to change to another directory of your choice).

Note: For an in-depth walkthrough of the TensorFlow Estimator API, see the tutorial "Creating Estimators in tf.estimator."
https://www.tensorflow.org/extend/estimators

## Set Up a Logging Hook

Since CNNs can take a while to train, let's set up some logging so we can track progress during training.
We can use TensorFlow's tf.train.SessionRunHook to create a tf.train.LoggingTensorHook that will log the probability values from the softmax layer of our CNN. Add the following to main():

    # Set up logging for predictions
      tensors_to_log = {"probabilities": "softmax_tensor"}
      logging_hook = tf.train.LoggingTensorHook(
          tensors=tensors_to_log, every_n_iter=50)
      
We store a dict of the tensors we want to log in tensors_to_log.
Each key is a label of our choice that will be printed in the log output, and the corresponding label is the name of a Tensor in the TensorFlow graph.
Here, our probabilities can be found in softmax_tensor, the name we gave our softmax operation earlier when we generated the probabilities in cnn_model_fn.

Note: If you don't explicitly assign a name to an operation via the name argument, TensorFlow will assign a default name.
A couple easy ways to discover the names applied to operations are to visualize your graph on TensorBoard) or to enable the TensorFlow Debugger (tfdbg).
Next, we create the LoggingTensorHook, passing tensors_to_log to the tensors argument. We set every_n_iter=50, which specifies that probabilities should be logged after every 50 steps of training.

## Train the Model

Now we're ready to train our model, which we can do by creating train_input_fn ans calling train() on mnist_classifier.
Add the following to main():

    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": train_data},
        y=train_labels,
        batch_size=100,
        num_epochs=None,
        shuffle=True)
    mnist_classifier.train(
        input_fn=train_input_fn,
        steps=20000,
        hooks=[logging_hook])
    
In the numpy_input_fn call, we pass the training feature data and labels to x (as a dict) and y, respectively.
We set a batch_size of 100 (which means that the model will train on minibatches of 100 examples at each step).
num_epochs=None means that the model will train until the specified number of steps is reached.
We also set shuffle=True to shuffle the training data.

In the train call, we set steps=20000 (which means the model will train for 20,000 steps total).
We pass our logging_hook to the hooks argument, so that it will be triggered during training.

## Evaluate the Model

Once training is complete, we want to evaluate our model to determine its accuracy on the MNIST test set.
We call the evaluate method, which evaluates the metrics we specified in eval_metric_ops argument in the model_fn.
Add the following to main():

    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": eval_data},
        y=eval_labels,
        num_epochs=1,
        shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)

To create eval_input_fn, we set num_epochs=1, so that the model evaluates the metrics over one epoch of data and returns the result.
We also set shuffle=False to iterate through the data sequentially.

## Run the Model

We've coded the CNN model function, Estimator, and the training/evaluation logic; now let's see the results. Run cnn_mnist.py.

Note: Training CNNs is quite computationally intensive.
Estimated completion time of cnn_mnist.py will vary depending on your processor, but will likely be upwards of 1 hour on CPU.
To train more quickly, you can decrease the number of steps passed to train(), but note that this will affect accuracy.
As the model trains, you'll see log output like the following:

    INFO:tensorflow:loss = 2.36026, step = 1
    INFO:tensorflow:probabilities = [[ 0.07722801  0.08618255  0.09256398, ...]]
    ...
    INFO:tensorflow:loss = 2.13119, step = 101
    INFO:tensorflow:global_step/sec: 5.44132
    ...
    INFO:tensorflow:Loss for final step: 0.553216.

    INFO:tensorflow:Restored model from /tmp/mnist_convnet_model
    INFO:tensorflow:Eval steps [0,inf) for training step 20000.
    INFO:tensorflow:Input iterator is exhausted.
    INFO:tensorflow:Saving evaluation summary for step 20000: accuracy = 0.9733, loss = 0.0902271
    {'loss': 0.090227105, 'global_step': 20000, 'accuracy': 0.97329998}

Here, we've achieved an accuracy of 97.3% on our test data set.